# Web scraping of .cif files

Goal: to get .cif files of a material in each space group from the TQC.org database.

## Method 2: scrap Materials Project

In [1]:
from mp_api.client import MPRester
import pyfplo.fedit as fedit
import pyfplo.fploio as fploio
import os
import shutil

/home/mi2/envs/venv_fplo/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
API_KEY = '7hwV32FqdTRd4JKCJn2qI30qDzYvLukG'  # log in to MP and look for it there
mpr = MPRester(API_KEY)

Let's retrieve the smallest number of sites for materials in each space group (interrupted, takes quite long...)

In [3]:
def num_materials_sg(num_sg):
    '''
    Number of materials found in the MP database for a SG
    '''
    materials = mpr.materials.summary.search(spacegroup_number=num_sg,
                                             num_magnetic_sites=0,
                                             theoretical=True)
    print(f'SG {num_sg}: {len(materials)} materials')

In [4]:
def printsettings(onlygroup=True):
    fio=fploio.FPLOInput('=.in')
    par=fio.parser()
    d=par()
    if not onlygroup:
        print( 'spacegroup setting: ',d('spacegroup.setting').S)
        print( 'lattice constants : ',d('lattice_constants').listS)
        print( 'axis angle        : ',d('axis_angles').listS)
        dw=d('wyckoff_positions')
        print( 'Wyckoff positions: ',dw.size())
        for i in range(dw.size()):
            taus=dw[i]('tau').listS
            print( '{0:>2s} {1:>20s} {2:>20s} {3:>20s}'.format(dw[i]('element').S,taus[0],taus[1],taus[2]))
    return int(d('spacegroup.number').S)

In [5]:
def convert_cifs_to_ins(list_sg=None):

    tol_wp = 1e-4
    
    list_failed = []
    list_wrong_sg = []

    if list_sg is None:
        list_sg = [i for i in range(1, 231)]
    
    for num_sg in list_sg:
    
        print(f'Nominal sg: {num_sg}')
        if num_sg == 168 or num_sg == 207: continue  # no material in MP for 168 :S
        
        try:
    
            # Create =.in if it doesn't exits, parse cif and write into =.in
            fio=fploio.FPLOInput('=.in')
            fio.structureFromCIFFile(f'{num_sg}.cif', wyckofftolerance=tol_wp, determinesymmetry=True)
            fio.writeFile("=.in")
                
            # Change other parameters in =.in
            fed=fedit.Fedit(recreate=False)
            fed.iteration(n=100)
            fed.relativistic('s')  # no SOC
            fed.vxc('5')
            fed.pipeFedit()
            
            # Print info about crystal
            num = printsettings()
            if num != num_sg:
                list_wrong_sg.append(num_sg)
            
            
            # Create sg_ directory and move =.in into it
            in_file = '=.in'
            dir = f'sg_{num_sg}'
            
            if not os.path.exists(dir):
                os.makedirs(dir)
            
            if os.path.exists(in_file):
                destination = os.path.join(dir, os.path.basename(in_file))
                shutil.move(in_file, destination)
            else:
                print('=.in file does not exist')

        except:
            list_failed.append(num_sg)

    return list_failed, list_wrong_sg

In [6]:
def cif2in(cif):
    tol_wp = 1e-4
    fio=fploio.FPLOInput('=.in')
    fio.structureFromCIFFile(cif, wyckofftolerance=tol_wp, determinesymmetry=True)
    fio.writeFile("=.in")

In [7]:
def parse_sg_in(root="."):
    fio=fploio.FPLOInput(root+'=.in')
    par=fio.parser()
    d=par()
    return int(d('spacegroup.number').S)

Find smallest number of sites for which a material exists within each SG:

In [10]:
d_num_sites = {}

In [11]:
for isg in range(1, 130):

    if isg in [168, 207]:
        continue

    num_materials = 0
    n_min = 2
    n_max = 3
    while num_materials == 0:
        n_min += 1
        n_max += 1
        materials = mpr.materials.summary.search(spacegroup_number=isg,
                                                 num_magnetic_sites=0,
                                                 num_sites=(n_min, n_max),
                                                 theoretical=True)
        num_materials = len(materials)
    print(f'SG {isg}: OK with {n_max}')
    d_num_sites[isg] = n_max

Retrieving SummaryDoc documents: 100%|██████████| 11/11 [00:00<00:00, 145543.67it/s]


SG 1: OK with 4


Retrieving SummaryDoc documents: 100%|██████████| 8/8 [00:00<00:00, 75743.64it/s]


SG 2: OK with 4


Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 100%|██████████| 5/5 [00:00<00:00, 44337.25it/s]


...

SG 127: OK with 6


Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 0it [00:00, ?it/s]
Retrieving SummaryDoc documents: 100%|██████████| 4/4 [00:00<00:00, 37957.50it/s]


SG 128: OK with 18


Retrieving SummaryDoc documents: 100%|██████████| 17/17 [00:00<00:00, 158804.38it/s]

SG 129: OK with 4


In [12]:
count = 0
for isg in d_num_sites:
    if d_num_sites[isg] < 12:
        count += 1
count

152

For each SG, get hte cif of a material with smallest number of sites, generate the =.in and check that the SG if correct

In [ ]:
list_ok = []
list_not_ok = []

for isg in range(1, 231):
    num_sites = d_num_sites[isg]
    if num_sites > 10:
        continue
    materials = mpr.materials.summary.search(spacegroup_number=isg,
                                             num_magnetic_sites=0,
                                             num_sites=(num_sites-1, num_sites),
                                             theoretical=True)
    for mat in materials:
        id = mat.material_id
        cif = f"{isg}_{id}.cif"
        structure = mpr.get_structure_by_material_id(id)
        structure.to(filename=cif, fmt="cif")
        try:
            cif2in(cif)
        except:
            continue

        # Check SG in =.in
        sg_in = parse_sg_in()
        if sg_in == isg:
            directory = f'sg_{isg}'
            os.makedirs(directory, exist_ok=True)
            destination = os.path.join(directory, cif)
            shutil.move(cif, destination)
            destination = os.path.join(directory, '=.in')
            shutil.move('=.in', destination)
            list_ok.append(isg)
            break
        else:
            os.remove(cif)
        list_not_ok.append(isg)

Retrieving MaterialsDoc documents: 100%|██████████| 1/1 [00:00<00:00, 7557.30it/s]


: 'xyz-symbols'


CPU TIME determineSiteOperations:  0.00 sec 
CPU TIME analyseGroup:  0.00 sec 

 Lattice type or lattice constants changed!
 Will take default values for bandplot special symmetry points!
 number of Wyckoff positions changed!
 Will take default concentrations and initial_spin_split!


------------------------------------------------------------------------
Blocks contained in cif file '2_mp-796077.cif':
------------------------------------------------------------------------
symmetry block No.   name
------------------------------------------------------------------------
     0               mno2
------------------------------------------------------------------------
blockswithsymdata [0 ] 

Symmetry information for datablock: mno2
Space group number: 1
Name-Hall         : not found
xyz-symbol        :  gives hallsymbol P 1

The following symmetry options are available:
  0 'xyz-symbols'

Getting structure from symmetry option: 'xyz-symbols'


op      =
            

Retrieving MaterialsDoc documents: 100%|██████████| 1/1 [00:00<00:00, 4963.67it/s]


roup number: 1
Name-Hall         : not found
xyz-symbol        :  gives hallsymbol P 1

The following symmetry options are available:
  0 'xyz-symbols'

Getting structure from symmetry option: 'xyz-symbols'


CPU TIME determineSiteOperations:  0.00 sec 
CPU TIME analyseGroup:  0.00 sec 

 Lattice type or lattice constants changed!
 Will take default values for bandplot special symmetry points!
 Element at some Wyckoff position changed!
 Will take default concentration and initial_spin_split!


------------------------------------------------------------------------
Blocks contained in cif file '1_mp-1239183.cif':
------------------------------------------------------------------------
symmetry block No.   name
------------------------------------------------------------------------
     0               mos3
------------------------------------------------------------------------
blockswithsymdata [0 ] 

Symmetry information for datablock: mos3
Space group number: 1
Name-Hall         : 

Retrieving MaterialsDoc documents: 100%|██████████| 1/1 [00:00<00:00, 7796.10it/s]


...

Retrieving MaterialsDoc documents: 100%|██████████| 1/1 [00:00<00:00, 9642.08it/s]


--------------
     0               landn2
------------------------------------------------------------------------
blockswithsymdata [0 ] 

Symmetry information for datablock: landn2
Space group number: 1
Name-Hall         : not found
xyz-symbol        :  gives hallsymbol P 1

The following symmetry options are available:
  0 'xyz-symbols'

Getting structure from symmetry option: 'xyz-symbols'


op      =
             0.454715308143480              0.742704363104845             -0.491552863449097
             0.742704363104845             -0.620812561820812             -0.250962132821879
            -0.491552863449097             -0.250962132821879             -0.833902746322668 
op_a    =
             1.000000000000000              0.999999456725069             -0.000000900202716
            -0.000000000000000             -1.000000000000000              0.000000000000000
             0.000000000000000             -0.000000000000000             -1.000000000000000 
op_a_int=
    1     

Retrieving MaterialsDoc documents: 100%|██████████| 1/1 [00:00<00:00, 8289.14it/s]


SiteOperations:  0.00 sec 
CPU TIME analyseGroup:  0.00 sec 

 Lattice type or lattice constants changed!
 Will take default values for bandplot special symmetry points!
 Element at some Wyckoff position changed!
 Will take default concentration and initial_spin_split!


------------------------------------------------------------------------
Blocks contained in cif file '166_mp-1222701.cif':
------------------------------------------------------------------------
symmetry block No.   name
------------------------------------------------------------------------
     0               latms2
------------------------------------------------------------------------
blockswithsymdata [0 ] 

Symmetry information for datablock: latms2
Space group number: 1
Name-Hall         : not found
xyz-symbol        :  gives hallsymbol P 1

The following symmetry options are available:
  0 'xyz-symbols'

Getting structure from symmetry option: 'xyz-symbols'


CPU TIME determineSiteOperations:  0.00 sec 
CP

Retrieving MaterialsDoc documents: 100%|██████████| 1/1 [00:00<00:00, 9489.38it/s]